In [ ]:
import obspy as op
import numpy as np
import cartopy
import cartopy.crs as ccrs
from obspy.clients.fdsn import Client
import cartopy.feature as cfeature
from obspy import UTCDateTime
from matplotlib.animation import FuncAnimation
import cartopy.feature as cfeature
import cartopy.io.img_tiles as cimgt
from cartopy.mpl.geoaxes import GeoAxes
from cartopy.mpl.gridliner import LATITUDE_FORMATTER, LONGITUDE_FORMATTER

import matplotlib.pyplot as plt
%matplotlib inline
%config InlineBackend.figure_format = 'retina'

import datetime

In [ ]:
currentDT = datetime.datetime.now()
print ('Download initiated.')
print ('Download began: ',str(currentDT))

client = Client("NCEDC")
t1 = op.UTCDateTime("1976-05-01T00:00:00") #start time of the request
t2 = op.UTCDateTime("2023-11-10T09:00:00") #end time of the request
minLat = 38.6834
maxLat = 38.924
minLon = -123.0541
maxLon = -122.5772
minMag = 2.0
catalog_ncedc = client.get_events(starttime=t1, endtime=t2, minlatitude=minLat, maxlatitude=maxLat,
minlongitude=minLon, maxlongitude=maxLon, minmagnitude=minMag)

currentDT = datetime.datetime.now()
print ('Download ended: ',str(currentDT))

In [ ]:
currentDT = datetime.datetime.now()
print ('Download initiated.')
print ('Download began: ',str(currentDT))

client = Client("IRIS")
t1 = op.UTCDateTime("1976-05-01T00:00:00") #start time of the request
t2 = op.UTCDateTime("2023-11-10T09:00:00") #end time of the request
minLat = 38.6834
maxLat = 38.924
minLon = -123.0541
maxLon = -122.5772
minMag = 2.0
catalog_iris = client.get_events(starttime=t1, endtime=t2, minlatitude=minLat, maxlatitude=maxLat,
minlongitude=minLon, maxlongitude=maxLon, minmagnitude=minMag)

currentDT = datetime.datetime.now()
print ('Download ended: ',str(currentDT))

In [ ]:
# Combine catalogs
catalog = catalog_ncedc + catalog_iris

In [ ]:
print('Number of events:',len(catalog.events))

In [ ]:
fig = plt.figure(figsize=(50,30))
ax = fig.add_subplot(1, 1, 1, projection=ccrs.PlateCarree())
ax.set_extent([minLon,maxLon,minLat,maxLat], crs=ccrs.PlateCarree())
ax.gridlines()

import cartopy.io.img_tiles as cimgt
request = cimgt.GoogleTiles()
ax.add_feature(cfeature.BORDERS, linestyle=':')
ax.add_image(request, 8)

gl = ax.gridlines(crs=ccrs.PlateCarree(), draw_labels=True,
                  linewidth=2, color='gray', alpha=0.5, linestyle='--')
gl.top_labels = False
gl.right_labels = False
gl.xformatter = LONGITUDE_FORMATTER
gl.yformatter = LATITUDE_FORMATTER
ax.add_feature(cartopy.feature.COASTLINE)

for event in catalog:
    lon = event.origins[0].longitude
    lat = event.origins[0].latitude
    ax.scatter(lon, lat, c='pink', edgecolor='black', s=500, transform=ccrs.PlateCarree())
    
    

In [ ]:
import matplotlib.dates as mdates

years=np.arange(1976,2024,1)
Nevents = np.zeros(len(years))
events_year = [event.origins[0].time.datetime for event in catalog]
plt.rcParams['figure.figsize'] = [15, 5]
plt.hist(events_year, bins=350, color = 'pink',edgecolor = 'black')
plt.gca().xaxis.set_major_locator(mdates.YearLocator())
plt.xticks(rotation=45)
plt.title('Earthquakes above M 2.0 in The Geysers region')
plt.xlabel('Year')
plt.ylabel('Number of Earthquakes')

In [ ]:
from matplotlib.animation import FFMpegWriter
import matplotlib.pyplot as plt
import cartopy
import cartopy.crs as ccrs
import cartopy.feature as cfeature
import cartopy.io.img_tiles as cimgt
from cartopy.mpl.geoaxes import GeoAxes
from cartopy.mpl.gridliner import LATITUDE_FORMATTER, LONGITUDE_FORMATTER

metadata = dict(title='Induced EQ', artist='matplot', comment='Induced EQ')
writer = FFMpegWriter(fps=15, metadata=metadata)
fig = plt.figure(figsize=(10, 10))

# Group events by month and year
events_by_month_year = {}
for event in reversed(catalog):
    month = event.origins[0].time.month
    year = event.origins[0].time.year
    key = (year, month)
    if key not in events_by_month_year:
        events_by_month_year[key] = []
    events_by_month_year[key].append(event)

with writer.saving(fig, "Induced_Earthquakes month label magnitude.mp4", dpi=200):
    ax = fig.add_subplot(1, 1, 1, projection=ccrs.PlateCarree())
    ax.set_extent([minLon, maxLon, minLat, maxLat], crs=ccrs.PlateCarree())
    ax.gridlines()
    request = cimgt.GoogleTiles()
    ax.add_feature(cfeature.BORDERS, linestyle=':')
    ax.add_image(request, 8)
    
    # Distance scale
    gl = ax.gridlines(crs=ccrs.PlateCarree(), draw_labels=True,
                      linewidth=2, color='gray', alpha=0.5, linestyle='--')
    gl.top_labels = False
    gl.right_labels = False
    gl.xformatter = LONGITUDE_FORMATTER
    gl.yformatter = LATITUDE_FORMATTER
    ax.add_feature(cartopy.feature.COASTLINE)

    for (year, month), events in events_by_month_year.items():
        ax = fig.add_subplot(1, 1, 1, projection=ccrs.PlateCarree())
        ax.set_extent([minLon, maxLon, minLat, maxLat], crs=ccrs.PlateCarree())
        ax.gridlines()
        ax.add_feature(cfeature.BORDERS, linestyle=':')
        ax.add_image(request, 8)
        
        ax.text(0.5, 0.95, f'{year}-{month}', horizontalalignment='center', verticalalignment='center',
        transform=ax.transAxes, fontsize=12, bbox=dict(facecolor='white', edgecolor='white', boxstyle='round,pad=0.5'))

        for event in events:
            lon = event.origins[0].longitude
            lat = event.origins[0].latitude
            magnitude = event.magnitudes[0].mag  # Assuming the magnitude is stored in the event
            alpha_value = 0.8 
            scale_factor = 100  # Adjust this factor to control the size of the dots
            dot_size = magnitude * scale_factor
            ax.scatter(lon, lat, c='pink', edgecolor='black', s=dot_size, alpha=alpha_value, transform=ccrs.PlateCarree())
            #ax.scatter(lon, lat, c='pink', edgecolor='black', s=200, transform=ccrs.PlateCarree())
            plt.pause(0.05)
            writer.grab_frame()
        
        ax.clear()  # Clear the map for each month

In [ ]:
# from matplotlib.animation import FFMpegWriter
# import matplotlib.pyplot as plt
# import cartopy.crs as ccrs
# import cartopy.feature as cfeature
# import cartopy.io.img_tiles as cimgt
# from cartopy.mpl.geoaxes import GeoAxes
# from cartopy.mpl.gridliner import LATITUDE_FORMATTER, LONGITUDE_FORMATTER

# metadata = dict(title='Induced EQ', artist='matplot', comment='Induced EQ')
# writer = FFMpegWriter(fps=15, metadata=metadata)
# fig = plt.figure(figsize=(10, 10))

# with writer.saving(fig, "Induced_Earthquakes.mp4", dpi=200):
#     ax = fig.add_subplot(1, 1, 1, projection=ccrs.PlateCarree())
#     ax.set_extent([minLon, maxLon, minLat, maxLat], crs=ccrs.PlateCarree())
#     ax.gridlines()

#     request = cimgt.GoogleTiles()
#     ax.add_feature(cfeature.BORDERS, linestyle=':')
#     ax.add_image(request, 8)
    
#     i = 0

#     for event in catalog:
#         lon = event.origins[0].longitude
#         lat = event.origins[0].latitude
#         i += 1
#         print(i)
#         ax.scatter(lon, lat, c='pink', edgecolor='black', s=500, transform=ccrs.PlateCarree())
#         plt.pause(0.05)
#         writer.grab_frame()